### Analyzing Data from an Ecommerce Shop

In [1]:
import pandas as pd
import numpy as np

from datetime import datetime
from datetime import date

import matplotlib.pyplot as plt
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from plotly.offline import plot


df = pd.read_csv('./data/data.csv', sep= ';')

The following data is from an ecommerce shop and shows the shows the shop visitors id, birth date, score, rank and whether an item was purchased or not.

In [2]:
df.head()

id  score  birth_date   rank  purchase
0  126181   1469    19690627   9771         0
1  153736    156     1984625  66676         0
2   45288   1406    19891123  10391         0
3   87765    206    19821211  53522         0
4   47516    273      195969  43468         0

Clean the data by removing corrupt data entries. Several customers had given corrupt birth days.

In [3]:
def get_age(birth_date):
    """ Source: https://stackoverflow.com/questions/52753613/grouping-categorising-ages-column-in-python-pandas """
    try:
        born = datetime.strptime(str(birth_date), '%Y%m%d')
        today = date.today()
        age = today.year - born.year - ((today.month, today.day) < (born.month, born.day))

    except (ValueError) as e:
        age = np.nan

    return age

In [4]:
df.insert(5, 'age', df['birth_date'].apply(get_age), True)
df.reset_index(drop=True, inplace=True)

Next step is to categorize the age data into categorical age bins:

In [5]:
bins = [20, 30, 40, 50, 60, 70, 100]
labels = ['20-30', '30-40', '40-50', '50-60', '60-70', '>70']
df['age_group'] = pd.cut(df['age'], bins=bins, labels=labels, right=False)

print(f"Number of corrupt birth dates removed, after adding age categories: {df['age'].isna().sum()}")
df.dropna(subset = ["age"], inplace=True)
print(f"Rows: {df.shape[0]}")

Number of corrupt birth dates removed, after adding age categories: 924
Rows: 88076


### Part I: How are rank and purchase likelihood related?
Having a look at the correlation matrix just gives a rough estimate how the likelyhood to purchase is related to the score value. There is a slight correlation of 0.15. However, this value doesn't account for e.g. non-linear relation.

In [6]:
df.corr()

id     score  birth_date      rank  purchase       age
id          1.000000 -0.005170   -0.003942 -0.001379  0.000820 -0.010300
score      -0.005170  1.000000   -0.005533 -0.635556  0.149567  0.088924
birth_date -0.003942 -0.005533    1.000000  0.004384  0.002909 -0.006974
rank       -0.001379 -0.635556    0.004384  1.000000 -0.136126 -0.141271
purchase    0.000820  0.149567    0.002909 -0.136126  1.000000 -0.020166
age        -0.010300  0.088924   -0.006974 -0.141271 -0.020166  1.000000

In [7]:
fig = px.scatter(x=df["score"], y=df['rank']).update_layout(
    xaxis_title="rank", yaxis_title="score"
    )

fig.update_traces(marker_line_color='rgb(0,0,0)', marker_line_width=1, opacity=0.70)
fig.update_layout(
    legend_title_text='age',
    )
fig.show()

In [8]:
num_bins = 30
bins = []
df['bins'] = pd.cut(df.score, num_bins)

for i in pd.unique(df['bins']):
    bins.append(str(i))

df_copy_for_sum = df.copy()
df_copy_for_sum = df_copy_for_sum.groupby(pd.cut(df_copy_for_sum.score, num_bins-1)).count()
sums = []
for i in df_copy_for_sum['purchase']:
    sums.append(i)
    
df2 = df.groupby(pd.cut(df.score, num_bins-1)).mean()

fig = go.Figure(data=go.Scatter(x = bins,
    y = df2["rank"], text=[str(i/sum(sums)*100) for i in sums],
    marker = dict(size=[i/sum(sums)*100 for i in sums],
    color = px.colors.qualitative.Set3),
    mode = 'markers'
    ))
fig.update_xaxes(showgrid=True, linewidth=1, linecolor='LightGrey', title_text="Score",
                 gridwidth=1, gridcolor='LightGrey', mirror=True, ticks='outside', showline=True)
fig.update_yaxes(title_text="Rank",
                 showgrid=True, linewidth=1, linecolor='LightGrey',
                 gridwidth=1, gridcolor='LightGrey', mirror=True, ticks='outside', showline=True)

fig.update_traces(marker_line_color='rgb(0,0,0)',
                  marker_line_width=1, opacity=0.90)
fig.update_layout(
    legend_title_text='age',
    plot_bgcolor='rgba(0,0,0,0)'
)
fig.show()


### Part II: How many visitors would have bought, if just the better half (better ranking) would have been targeted?

In [9]:
df_3 = df[(df['rank'] <= df['rank'].max()/2) & (df['purchase'] == 1)]
df_3.shape[0]

5944

In [10]:
df_3 = df[(df['rank'] > df['rank'].max()/2) & (df['purchase'] == 1)]
df_3.shape[0]

3074

2/3 of the shop visitors purchase an item from the online store, if they are in the first half of the ranking. Therfore, targeting this group is expected leading to better sales.

### Part III: How is the customers age affecting the possibility to purchase in the online shop? 

Next we would like to know how the age distribution of actual buyers looks like.

In [11]:
df1 = df.loc[df['purchase'] == 1].groupby(['age_group']).agg({'age_group': 'count'})

p_buy = df.loc[df['purchase'] == 1].shape[0]/df.shape[0]


age_distr_all = df.groupby(['age_group'])['age_group'].count()#.div(df.shape[0])
age_distr_all = age_distr_all/age_distr_all.sum()

age_distr_buyer = df1['age_group'].div(df1['age_group'].sum())
p_age_buy = p_buy* age_distr_all


frame = { '$$P(age)$$': age_distr_all, '$$P(age\cap buy)$$': age_distr_buyer, '$$P(age|buy)$$': p_age_buy }
result = pd.DataFrame(frame)

result.rename_axis("$$age$$", inplace=True)
result

$$P(age)$$  $$P(age\cap buy)$$  $$P(age|buy)$$
$$age$$                                                
20-30      0.048755            0.047487        0.004992
30-40      0.179398            0.195273        0.018368
40-50      0.353104            0.356041        0.036154
50-60      0.290146            0.295129        0.029708
60-70      0.094352            0.081993        0.009661
>70        0.034246            0.024076        0.003506

In [12]:
print(f"{round(100*p_buy,2)}% of all visitors are buying in the online shop.")

10.24% of all visitors are buying in the online shop.


The table above shows the probabilites of shop visitors to buy based on their age. $P(age)$ is the likelihood that a shop visitors is a certain age. $P(age\cap buy)$ is the likelihood that a shop visitors age intersects with purchasing an item. $P(age|buy)$ is the possibilty that a online shop vistor is a certain age and has purchased in the shop. Summing up all these values, 10.24% of all visitors end up buying in the online store.

Of all the people buying in the online shop, the visitors from age group 40-50 are the most likely buyers. Therfore, it makes sense to specifically target those customers more effectivly. This group accounts for more than a third of all the sales. From a demographic perspective this group has the most wealth and is worth to be focused on.

In [13]:
fig = px.pie(df1, values=df1['age_group'], 
             color_discrete_sequence=px.colors.qualitative.Set3,
             names=df1.index ,
             hole=.35)
fig.update_traces(hoverinfo='label+percent', marker=dict(colors=px.colors.qualitative.Pastel, line=dict(width=1)))
fig.update_layout(
    legend_title_text='Age classification',
    title_text=f"Age distribution of shop visitors that bought from the shop"
    )
fig.show()